In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, LSTM
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import load_model
from tensorflow.keras.optimizers import Adam  # Make sure to use TensorFlow's Adam optimizer
from sklearn.model_selection import train_test_split
import pickle
import re
import nltk

nltk.download("punkt")
nltk.download("stopwords")


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\ormec\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ormec\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [2]:
WPT = nltk.WordPunctTokenizer()
stopwordlist = nltk.corpus.stopwords.words("english")
stopwordlist

['i',
 'me',
 'my',
 'myself',
 'we',
 'our',
 'ours',
 'ourselves',
 'you',
 "you're",
 "you've",
 "you'll",
 "you'd",
 'your',
 'yours',
 'yourself',
 'yourselves',
 'he',
 'him',
 'his',
 'himself',
 'she',
 "she's",
 'her',
 'hers',
 'herself',
 'it',
 "it's",
 'its',
 'itself',
 'they',
 'them',
 'their',
 'theirs',
 'themselves',
 'what',
 'which',
 'who',
 'whom',
 'this',
 'that',
 "that'll",
 'these',
 'those',
 'am',
 'is',
 'are',
 'was',
 'were',
 'be',
 'been',
 'being',
 'have',
 'has',
 'had',
 'having',
 'do',
 'does',
 'did',
 'doing',
 'a',
 'an',
 'the',
 'and',
 'but',
 'if',
 'or',
 'because',
 'as',
 'until',
 'while',
 'of',
 'at',
 'by',
 'for',
 'with',
 'about',
 'against',
 'between',
 'into',
 'through',
 'during',
 'before',
 'after',
 'above',
 'below',
 'to',
 'from',
 'up',
 'down',
 'in',
 'out',
 'on',
 'off',
 'over',
 'under',
 'again',
 'further',
 'then',
 'once',
 'here',
 'there',
 'when',
 'where',
 'why',
 'how',
 'all',
 'any',
 'both',
 'each

In [3]:
import pickle
dataset = pd.read_pickle("merged_training.pkl")
dataset

text emotions
27383   i feel awful about it too because it s my job ...  sadness
110083                              im alone i feel awful  sadness
140764  ive probably mentioned this before but i reall...      joy
100071           i was feeling a little low few days back  sadness
2837    i beleive that i am much more sensitive to oth...     love
...                                                   ...      ...
566     that was what i felt when i was finally accept...      joy
36236   i take every day as it comes i m just focussin...     fear
76229       i just suddenly feel that everything was fake  sadness
131640  im feeling more eager than ever to claw back w...      joy
64703   i give you plenty of attention even when i fee...  sadness

[416809 rows x 2 columns]

In [4]:
dataset["emotions"].unique()

array(['sadness', 'joy', 'love', 'anger', 'fear', 'surprise'],
      dtype=object)

In [5]:
dataset.columns

Index(['text', 'emotions'], dtype='object')

In [6]:
dataset.head(10)

text emotions
27383   i feel awful about it too because it s my job ...  sadness
110083                              im alone i feel awful  sadness
140764  ive probably mentioned this before but i reall...      joy
100071           i was feeling a little low few days back  sadness
2837    i beleive that i am much more sensitive to oth...     love
18231   i find myself frustrated with christians becau...     love
10714   i am one of those people who feels like going ...      joy
35177   i feel especially pleased about this as this h...      joy
122177  i was struggling with these awful feelings and...      joy
26723     i feel so enraged but helpless at the same time    anger

In [7]:
#Noktalamaların temizlenmesi 
dataset["emotions"] = dataset["emotions"].apply(lambda x:re.sub('[,\.!?:()@_"]','',x))
dataset["emotions"] = dataset["emotions"].apply(lambda x: re.sub('@', ' ', x))
dataset["emotions"] = dataset["emotions"].apply(lambda x: re.sub(r'[^a-zA-Z0-9\s]', '', x))


#Büyük harf küçük harfe
dataset["emotions"] = dataset["emotions"].apply(lambda x:x.lower())

#Boşlukların temizlenmesi
#dataset["emotions"] = dataset["emotions"].apply(lambda x:x.strip())
dataset["emotions"] = dataset["emotions"].apply(lambda x: re.sub(" +", " ", x))

#Etkisiz kelimelerin kaldırılması
def token(values):
  words = nltk.tokenize.word_tokenize(values)
  stop_words = nltk.corpus.stopwords.words('turkish')
  filtered_words = [word for word in words if word not in stop_words]
  not_stopword_doc = "".join(filtered_words)
  return not_stopword_doc

dataset["emotions"] = dataset["emotions"].apply(lambda x: token(x))
dataset

text emotions
27383   i feel awful about it too because it s my job ...  sadness
110083                              im alone i feel awful  sadness
140764  ive probably mentioned this before but i reall...      joy
100071           i was feeling a little low few days back  sadness
2837    i beleive that i am much more sensitive to oth...     love
...                                                   ...      ...
566     that was what i felt when i was finally accept...      joy
36236   i take every day as it comes i m just focussin...     fear
76229       i just suddenly feel that everything was fake  sadness
131640  im feeling more eager than ever to claw back w...      joy
64703   i give you plenty of attention even when i fee...  sadness

[416809 rows x 2 columns]

In [8]:
tweet = dataset["emotions"].values.tolist()
sentiment = dataset["emotions"].values.tolist()
print(sentiment)

for n, i in enumerate(sentiment):
    if i == 'sadness':
        sentiment[n] = 0
    elif i == 'joy':
        sentiment[n] = 1
    elif i == 'love':
        sentiment[n] = 2
    elif i == 'anger':
        sentiment[n] = 3
    elif i == 'fear':
        sentiment[n] = 4
    elif i == 'surprise':
        sentiment[n] = 5

print(sentiment)

    
X_train,X_test,y_train,y_test = train_test_split(tweet,sentiment,test_size=0.2,random_state=42)

['sadness', 'sadness', 'joy', 'sadness', 'love', 'love', 'joy', 'joy', 'joy', 'anger', 'anger', 'sadness', 'joy', 'anger', 'anger', 'joy', 'sadness', 'fear', 'joy', 'love', 'sadness', 'sadness', 'fear', 'sadness', 'love', 'anger', 'joy', 'joy', 'sadness', 'sadness', 'joy', 'surprise', 'fear', 'joy', 'joy', 'love', 'sadness', 'joy', 'fear', 'joy', 'fear', 'sadness', 'joy', 'sadness', 'surprise', 'joy', 'fear', 'joy', 'anger', 'joy', 'joy', 'joy', 'sadness', 'anger', 'joy', 'love', 'love', 'sadness', 'sadness', 'sadness', 'joy', 'joy', 'joy', 'surprise', 'sadness', 'surprise', 'sadness', 'joy', 'surprise', 'sadness', 'fear', 'joy', 'joy', 'anger', 'sadness', 'anger', 'love', 'joy', 'fear', 'joy', 'fear', 'joy', 'sadness', 'sadness', 'joy', 'fear', 'joy', 'joy', 'sadness', 'sadness', 'joy', 'joy', 'sadness', 'anger', 'fear', 'joy', 'anger', 'sadness', 'sadness', 'joy', 'sadness', 'joy', 'sadness', 'fear', 'sadness', 'joy', 'sadness', 'joy', 'sadness', 'anger', 'fear', 'joy', 'fear', 'fear

In [9]:
dataset.head(15)

text emotions
27383   i feel awful about it too because it s my job ...  sadness
110083                              im alone i feel awful  sadness
140764  ive probably mentioned this before but i reall...      joy
100071           i was feeling a little low few days back  sadness
2837    i beleive that i am much more sensitive to oth...     love
18231   i find myself frustrated with christians becau...     love
10714   i am one of those people who feels like going ...      joy
35177   i feel especially pleased about this as this h...      joy
122177  i was struggling with these awful feelings and...      joy
26723     i feel so enraged but helpless at the same time    anger
41979                     i said feeling a bit rebellious    anger
2046    i also feel disillusioned that someone who cla...  sadness
98659   i mean is on this stupid trip of making the gr...      joy
50434   i woke up feeling particularly vile tried to i...    anger
9280    i could feel the vile moth burrowing its way i...    anger

In [10]:
from tensorflow.keras.preprocessing.text import Tokenizer

tokenizer = Tokenizer(num_words = 10000) #Metin parçasını böler.
tokenizer.fit_on_texts(tweet)
tokenizer.word_index

{'joy': 1, 'sadness': 2, 'anger': 3, 'fear': 4, 'love': 5, 'surprise': 6}

In [11]:
X_train_tokens = tokenizer.texts_to_sequences(X_train)
X_test_tokens = tokenizer.texts_to_sequences(X_test)
#Metin dizisi sayılara dönüşür . Bugün hava çok güzel cümlesi 0123 olarak ifade edilir.
num_tokens = [len(tokens) for tokens in X_train_tokens + X_test_tokens]
num_tokens = np.array(num_tokens)

max_tokens = np.mean(num_tokens) + 2*np.std(num_tokens) # Her cümle farklı uzunluktadır , ortalama bulunur ve her cümle
max_tokens = int(max_tokens)                            # ortalama uzaklığa getirilir.Aşağıda kodu görebilirsin.

num_tokens,max_tokens

(array([1, 1, 1, ..., 1, 1, 1]), 1)

In [12]:
X_train_padding = pad_sequences(X_train_tokens,maxlen=max_tokens)
X_test_padding = pad_sequences(X_test_tokens,maxlen=max_tokens)

X_test_padding[15]

array([1])

In [13]:
idx = tokenizer.word_index
inverse_map = dict(zip(idx.values(),idx.keys()))
def tokens_to_string(tokens):
    words = [inverse_map[token] for token in tokens in token!=0]
    text = ' '.join(words)
    return text             # Token halindeki veriler tekrar cümleye çevrilir.

In [14]:
import tensorflow as tf

model = Sequential()
embedding_dim = 100
model.add(Embedding(input_dim=10000,
                    output_dim=embedding_dim,
                    input_length=max_tokens,
                    name="embedding_layer"
                    ))

model.add(LSTM(units=32,return_sequences=True,dropout=0.4,recurrent_dropout=0.2))
model.add(LSTM(units=16,return_sequences=True,dropout=0.4,recurrent_dropout=0.2))
model.add(LSTM(units=8,dropout=0.4,recurrent_dropout=0.4))
model.add(Dense(6, activation='softmax'))

optimizer = tf.keras.optimizers.Adam(learning_rate=1e-3)

model.compile(loss='sparse_categorical_crossentropy', optimizer=optimizer, metrics=['accuracy'])


In [15]:
y_train = np.array(y_train)
history=model.fit(X_train_padding,y_train,validation_split=0.25,epochs=2,batch_size=8)

Epoch 1/2
31261/31261 [==============================] - 845s 27ms/step - loss: 0.0371 - accuracy: 0.9886 - val_loss: 3.9140e-05 - val_accuracy: 1.0000
Epoch 2/2
31261/31261 [==============================] - 768s 25ms/step - loss: 6.3913e-04 - accuracy: 0.9999 - val_loss: 7.2601e-06 - val_accuracy: 1.0000


In [16]:
y_test = np.array(y_test)
result = model.evaluate(X_test_padding,y_test)

2606/2606 [==============================] - 7s 3ms/step - loss: 7.2449e-06 - accuracy: 1.0000


In [17]:
model.save(f'../LSTM2_Saved')

INFO:tensorflow:Assets written to: ../LSTM2_Saved\assets


INFO:tensorflow:Assets written to: ../LSTM2_Saved\assets
